In [1]:
import nanopq
import numpy as np
import networkx as nx
from collections import defaultdict
from tqdm import tqdm
from sklearn.neighbors import NearestNeighbors
from sklearn.datasets import make_blobs


In [2]:
#random = np.random.default_rng(123)
#N, D = 100000, 128
#vectors = random.random((N, D)).astype(np.float32)

In [3]:
#for i in range(len(vectors) // 10):
#    vectors[i] = vectors[i] / 10
#for i in range(len(vectors) // 10, 2*len(vectors)// 10):
#    vectors[i] = vectors[i] / 10
#    vectors[i] += 0.1
#for i in range(2*len(vectors) // 10, 3*len(vectors)// 10):
#    vectors[i] = vectors[i] / 10
#    vectors[i] += 0.2
#for i in range(3*len(vectors) // 10, 4*len(vectors)// 10):
#    vectors[i] = vectors[i] / 10
#    vectors[i] += 0.3
#for i in range(4*len(vectors) // 10, 5*len(vectors)// 10):
#    vectors[i] = vectors[i] / 10
#    vectors[i] += 0.4
#for i in range(5*len(vectors) // 10, 6*len(vectors)// 10):
#    vectors[i] = vectors[i] / 10
#    vectors[i] += 0.5
#for i in range(6*len(vectors) // 10, 7*len(vectors)// 10):
#    vectors[i] = vectors[i] / 10
#    vectors[i] += 0.6
#for i in range(7*len(vectors) // 10, 8*len(vectors)// 10):
#    vectors[i] = vectors[i] / 10
#    vectors[i] += 0.7
#for i in range(8*len(vectors) // 10, 9*len(vectors)// 10):
#    vectors[i] = vectors[i] / 10
#    vectors[i] += 0.8
#for i in range(9*len(vectors) // 10, 10*len(vectors)// 10):
#    vectors[i] = vectors[i] / 10
#    vectors[i] += 0.9

In [4]:
#CLUSTERS_NUMBER = 1000
#for k in range(CLUSTERS_NUMBER):
#    for i in range(k * len(vectors) // CLUSTERS_NUMBER, (k+1) * len(vectors) // CLUSTERS_NUMBER):
#        vectors[i] = vectors[i] / 10
#        vectors[i] += (k / CLUSTERS_NUMBER)

In [5]:
N, D = 1000000, 128
CLUSTERS_NUMBER = 10000  # число групп
np.random.seed(0)
centers = np.random.randint(-2000, 2000, size=(CLUSTERS_NUMBER, D))  # создает K центров D-размерности, расположенных случайно

vectors, y = make_blobs(n_samples=N, n_features=D, centers=centers, random_state=0)
vectors = vectors.astype(np.float32)

In [6]:
#dists = np.linalg.norm(vectors[0] - vectors[1])

In [3]:
#import numpy as np
#import networkx as nx
#from sklearn.neighbors import NearestNeighbors
#from tqdm import tqdm
#
#def generate_vectors(n, dims=128):
#    vectors = np.random.rand(n, dims)
#    return vectors
#    
#def generate_graph(vectors, k_nearest):
#    nbrs = NearestNeighbors(n_neighbors=k_nearest, algorithm='ball_tree').fit(vectors)
#
#    G = nx.Graph()
#    for i, vector in tqdm(enumerate(vectors), total=len(vectors)):
#        indices = nbrs.kneighbors([vector], return_distance=False)[0]
#        for index in indices:
#            if index != i:
#                G.add_edge(i, index)
#    return G
#
#n = 10000  # количество вершин графа
#k = 15    # количество ближайших соседей для связывания вершин
#
## генерируем векторы
#vectors = generate_vectors(n)
#
## генерируем граф
#G = generate_graph(vectors, k)
#
## визуализируем граф
## nx.draw(G)

100%|██████████| 10000/10000 [00:09<00:00, 1091.70it/s]


In [70]:
import numpy as np
import networkx as nx
from sklearn.neighbors import NearestNeighbors
from tqdm import tqdm

def generate_vectors(n, dims=128):
    vectors = np.random.rand(n, dims)
    return vectors
    
def generate_graph(vectors, k_nearest):
    nbrs = NearestNeighbors(n_neighbors=k_nearest, algorithm='ball_tree').fit(vectors)
    indices = nbrs.kneighbors(vectors, return_distance=False)
    G = nx.Graph()
    for i in tqdm(range(len(vectors)), total=len(vectors)):
        for index in indices[i]:
            if index != i:
                G.add_edge(i, index)
    return G

#n = 10000  # количество вершин графа
k = 15    # количество ближайших соседей для связывания вершин

# генерируем векторы
#vectors = generate_vectors(n)

# генерируем граф
G = generate_graph(vectors, k)

# визуализируем граф
# nx.draw(G)

In [6]:
import numpy as np
import networkx as nx
import faiss
from tqdm import tqdm

def generate_vectors(n, dims=128):
    vectors = np.random.rand(n, dims)
    return vectors
    
def generate_graph(vectors, k_nearest):
    index = faiss.IndexFlatL2(vectors.shape[1])  # длина вектора
    index.add(vectors.astype('float32'))
    _, indices = index.search(vectors.astype('float32'), k_nearest)
    G = nx.Graph()
    for i in tqdm(range(len(vectors)), total=len(vectors)):
        for index in indices[i]:
            if index != i:
                G.add_edge(i, index)
    return G

#n = 10000  # количество вершин графа
k = 30    # количество ближайших соседей для связывания вершин

# генерируем векторы
#vectors = generate_vectors(n)

# генерируем граф
G = generate_graph(vectors, k)

# визуализируем граф
# nx.draw(G)

100%|██████████| 1000000/1000000 [00:37<00:00, 26361.98it/s]


In [78]:
#import numpy as np
#import networkx as nx
#from sklearn.neighbors import NearestNeighbors
#from multiprocessing import Pool
#
#def generate_graph(vectors, k_nearest):
#    G = nx.Graph()
#    with Pool() as p:
#        results = p.map(adding_edges, [(vectors, G, k_nearest, i) for i in range(len(vectors))])
#    return G
#
#def adding_edges(params):
#    vectors, G, k_nearest, i = params
#    nbrs = NearestNeighbors(n_neighbors=k_nearest, algorithm='ball_tree').fit(vectors)
#    vector = vectors[i]
#    indices = nbrs.kneighbors([vector], return_distance=False)[0]
#    for index in indices:
#        if index != i:
#            G.add_edge(i, index)
#
#k = 15    # количество ближайших соседей для связывания вершин
#
#
## генерируем граф
#G = generate_graph(vectors, k)

In [ ]:
#G = nx.Graph()
#G.add_nodes_from(range(0, N))
#
#for i in tqdm(range(len(vectors))):
#    dists = []
#    
#    for j in tqdm(range(i + 1, len(vectors))):
#        dist = np.linalg.norm(vectors[i] - vectors[j])
#        dists.append([dist, [i, j]])
#    dists.sort(key=lambda x:x[0])
#    
#    k = 0
#    while G.degree[i] < 5 and len(dists) > k:
#        edge = dists[k][1]
#        if G.degree[edge[0]] >= 5 or G.degree[edge[1]] >= 5:
#            k += 1
#            continue
#        if not G.has_edge(edge[0], edge[1]):
#            G.add_edge(edge[0], edge[1])
#        k += 1

In [11]:
#nx.write_gml(G, "graph.gml")
#G = nx.read_gml('graph.gml')

ERROR: Could not find a version that satisfies the requirement faiss-gpu (from versions: none)
ERROR: No matching distribution found for faiss-gpu


In [7]:
pq = nanopq.PQ(M=2, Ks=128, verbose=True)

pq.fit(vectors)

X_code = pq.encode(vectors)

M: 2, Ks: 128, metric : <class 'numpy.uint8'>, code_dtype: l2
iter: 20, seed: 123
Training the subspace: 0 / 2
Training the subspace: 1 / 2
Encoding the subspace: 0 / 2
Encoding the subspace: 1 / 2


In [8]:
indexes_map = defaultdict(list)

for i in range(len(X_code)):
    indexes_map[(X_code[i][0], X_code[i][1])].append(i)

In [7]:
indexes_map

defaultdict(list,
            {(37, 35): [0,
              1203,
              2049,
              7015,
              14488,
              15493,
              18035,
              31314,
              42815,
              44225,
              44685,
              56140,
              62543,
              82308,
              88008,
              98894,
              112011,
              112655,
              120292,
              124874,
              128035,
              130714,
              132291,
              134957,
              143820,
              143940,
              146197,
              149763,
              154514,
              158270,
              164196,
              169948,
              182675,
              189667,
              191938,
              192021,
              196322,
              197992,
              208595,
              208760,
              209023,
              215292,
              219491,
              219956,
              226876,
     

In [201]:
np.linalg.norm(vectors[1] - vectors[9999])

10.230643

In [10]:
pq.encode(np.array([vectors[0]]))

Encoding the subspace: 0 / 2
Encoding the subspace: 1 / 2


array([[37, 35]], dtype=uint8)

In [11]:
pq.encode(np.array([vectors[789242]]))


Encoding the subspace: 0 / 2
Encoding the subspace: 1 / 2


array([[37, 35]], dtype=uint8)

In [9]:
G.edges(0)

EdgeDataView([(0, 789242), (0, 209023), (0, 692169), (0, 143940), (0, 491302), (0, 845809), (0, 956944), (0, 985448), (0, 44685), (0, 130714), (0, 154514), (0, 273228), (0, 386988), (0, 520557), (0, 831782), (0, 2049), (0, 14488), (0, 15493), (0, 146197), (0, 290674), (0, 333644), (0, 338804), (0, 346819), (0, 352029), (0, 397329), (0, 459021), (0, 561696), (0, 621952), (0, 625185), (0, 1203), (0, 7015), (0, 44225), (0, 82308), (0, 128035), (0, 158270), (0, 208760), (0, 233399), (0, 248874), (0, 253368), (0, 299764), (0, 383116), (0, 408198), (0, 411940), (0, 436877), (0, 459484), (0, 498411), (0, 510784), (0, 629919), (0, 644720), (0, 650509), (0, 734669), (0, 765399), (0, 773620), (0, 783474), (0, 785898), (0, 803908), (0, 858478), (0, 889952), (0, 964273), (0, 987831)])

In [33]:
G.edges(881476)

EdgeDataView([(881476, 65093), (881476, 382618), (881476, 412096), (881476, 461660), (881476, 574825), (881476, 584982), (881476, 74524), (881476, 787560), (881476, 970517), (881476, 5012), (881476, 6455), (881476, 47815), (881476, 152748), (881476, 178022), (881476, 267768), (881476, 345062)])

In [166]:
random.random((1, D)).astype(np.float32)  # a 128-dim query vector

array([[0.25658694, 0.6091241 , 0.14374273, 0.53519887, 0.8697552 ,
        0.99257934, 0.6424963 , 0.01765927, 0.4461706 , 0.877323  ,
        0.89228606, 0.87773186, 0.5702696 , 0.615654  , 0.28585458,
        0.14148557, 0.04505728, 0.7141362 , 0.79332936, 0.7549821 ,
        0.6845735 , 0.17062017, 0.7901157 , 0.1856994 , 0.4578432 ,
        0.08367708, 0.94035923, 0.63893604, 0.00114968, 0.14276515,
        0.4243772 , 0.90295047, 0.5451599 , 0.37351525, 0.16187067,
        0.27219978, 0.6210516 , 0.7048894 , 0.82378304, 0.9656518 ,
        0.60560656, 0.9274007 , 0.31453627, 0.11334343, 0.5391487 ,
        0.94779766, 0.8646904 , 0.3276911 , 0.68516475, 0.6957105 ,
        0.13860202, 0.7679339 , 0.77817994, 0.7864451 , 0.30396876,
        0.5891602 , 0.32192856, 0.173497  , 0.11723366, 0.23589143,
        0.27263865, 0.6535606 , 0.2872451 , 0.64810616, 0.3581151 ,
        0.5051237 , 0.869978  , 0.6005067 , 0.3281642 , 0.6343794 ,
        0.01557175, 0.93019724, 0.8257041 , 0.79

In [12]:
def find_nearest(G, query, indexes_map=indexes_map, pq=pq, vectors=vectors):
    query_mi = pq.encode(query)
    query_mi_neighbours = indexes_map[(query_mi[0][0], query_mi[0][1])]
    best_node = query_mi_neighbours[0]
    best_dist = np.linalg.norm(vectors[best_node] - query)
    queue = []
    queue.append(best_node)
    was = set()
    was.add(best_node)
    while len(queue) > 0:
        node = queue.pop(0)
        for edge in G.edges(node):
            node = edge[1]
            if node in was:
                continue
            was.add(node)
            dist = np.linalg.norm(vectors[node] - query)
            if dist < best_dist:
                queue.append(node)
                best_node = node
                best_dist = dist
    return best_node, best_dist


In [16]:
find_nearest(G, np.array([vectors[6565]]))

Encoding the subspace: 0 / 2
Encoding the subspace: 1 / 2


(6565, 0.0)

In [39]:
np.linalg.norm(np.array([vectors[0]]) - np.array([vectors[0]]))

0.0

HNSW

In [20]:
index = faiss.IndexHNSWFlat(D, CLUSTERS_NUMBER)

print(index.ntotal)   # 0
index.add(vectors)
print(index.ntotal)   # 1000000

In [19]:
topn = 7
D, I = index.search(vectors[:5], topn)  # Возвращает результат: Distances, Indices
print(I)
print(D)

NameError: name 'query' is not defined